# Extract Tweets from Twitter Stream Grab

In [1]:
import zipfile
import tarfile
import bz2
import json
import pandas as pd
from tqdm import tqdm as tq
import gzip 
import glob
import os

def save_tweets(tweets, filname):
    with gzip.open(filname, 'wt', encoding='UTF-8') as zipfile:
        for tweet in tq(tweets, desc='Saving ' + filname.split('/')[-1]):
            zipfile.write(json.dumps(tweet)+'\r\n')

def extract_tweets_from_file(myfile):
    tweets = []
    content = bz2.decompress(myfile.read())
    for line in content.decode('utf8').split('\r\n'):
        if not line.strip():
            continue
        try: 
            data = json.loads(line.strip())
            in_russian = 'lang' in data and data['lang'] == 'ru' 
            is_retweet = 'retweeted_status' in data
            if in_russian and not is_retweet:
                tweets.append(data)
        except:
            print('json parsing error: ')
    return tweets
    
def extract_tweets_for_day_from_zip(path):
    tweets = []
    with zipfile.ZipFile(path, 'r') as myzip:
        tweet_dumps = [filename for filename in myzip.namelist() if 'json.bz2' in filename]
        for filename in tq(tweet_dumps, desc='Parsing ' + path.split('/')[-1], leave=False):
            with myzip.open(filename, 'r') as myfile:
                extracted_tweets = extract_tweets_from_file(myfile)
                tweets.extend(extracted_tweets)
    return tweets

def extract_tweets_for_day_from_tar(path):
    tweets = []
    with tarfile.TarFile(path, 'r') as mytar:
        tweet_dumps = [filename for filename in mytar.getmembers() if 'json.bz2' in filename.name]
        for filename in tq(tweet_dumps, desc='Parsing ' + path.split('/')[-1], leave=False):
            with mytar.extractfile(filename) as myfile:
                extracted_tweets = extract_tweets_from_file(myfile)
                tweets.extend(extracted_tweets)
    return tweets

def extract_tweets_with_location_for_month(directory, path):
    if not os.path.exists(directory):
        os.makedirs(directory)
    archive_file_paths_zip = sorted(glob.glob(path+"*.zip", recursive=True))
    archive_file_paths_tar = sorted(glob.glob(path+"*.tar", recursive=True))
    if len(archive_file_paths_zip) != 0:
        for file_path in tq(archive_file_paths_zip, desc='Parsing *.zip'+path.split('/')[-2]):
            name = file_path.split('/')[-1].split('.')[0]
            tweets = extract_tweets_for_day_from_zip(file_path)
            save_tweets(tweets, directory+'/'+name+'_full_ru.json.gz2')
            print('saved: ' + name)
    else:
        for file_path in tq(archive_file_paths_tar, desc='Parsing *.tar'+path.split('/')[-2]):
            name = file_path.split('/')[-1].split('.')[0]
            tweets = extract_tweets_for_day_from_tar(file_path)
            save_tweets(tweets, directory+'/'+name+'_full_ru.json.gz2')
            print('saved: ' + name)

In [4]:
extract_tweets_with_location_for_month(
    'archiveteam-twitter-stream-2020-01',
    '/Volumes/TOSHIBA EXT/twitter-stream-2020/archiveteam-twitter-stream-2020-01/',
)

Parsing *.tararchiveteam-twitter-stream-2020-01:   0%|          | 0/31 [00:00<?, ?it/s]
Parsing twitter_stream_2020_01_01.tar:   6%|▌         | 87/1440 [01:07<21:43,  1.04it/s]


Parsing twitter_stream_2020_01_01.tar:  12%|█▏        | 175/1440 [02:18<14:14,  1.48it/s]


Parsing twitter_stream_2020_01_01.tar:  18%|█▊        | 263/1440 [03:16<12:38,  1.55it/s]


Parsing twitter_stream_2020_01_01.tar:  24%|██▍       | 351/1440 [04:29<21:44,  1.20s/it]


Parsing twitter_stream_2020_01_01.tar:  30%|███       | 439/1440 [06:11<16:58,  1.02s/it]


...

Parsing twitter_stream_2020_01_31.tar:  93%|█████████▎| 1316/1411 [34:49<02:37,  1.66s/it]


Parsing twitter_stream_2020_01_31.tar:  99%|█████████▉| 1403/1411 [37:26<00:17,  2.19s/it]


Parsing twitter_stream_2020_01_31.tar: 100%|██████████| 1411/1411 [37:40<00:00,  1.79s/it]
                                                                                          
Saving twitter_stream_2020_01_31_full_ru.json.gz2:   0%|          | 0/13965 [00:00<?, ?it/s]
Saving twitter_stream_2020_01_31_full_ru.json.gz2:   1%|          | 170/13965 [00:00<00:08, 1690.03it/s]
Saving twitter_stream_2020_01_31_full_ru.json.gz2:   2%|▏         | 339/13965 [00:00<00:08, 1684.23it/s]
Saving twitter_stream_2020_01_31_full_ru.json.gz2:   4%|▎         | 512/13965 [00:00<00:07, 1697.57it/s]
Saving twitter_stream_2020_01_31_full_ru.json.gz2:   5%|▍         | 681/13965 [00:00<00:07, 1691.64it/s]
Saving twitter_stream_2020_01_31_full_ru.json.gz2:   6%|▌         | 849/13965 [00:00<00:07, 1686.93it/s]
Saving twitter_stream_2020_01_31_full_ru.json.gz2:   7%|▋         | 992/13965 [00:00<00:08, 1599.63it/s]
Saving twitter_stream_2020_01_31_full_ru.json.gz2:   8%|▊         | 1134/13965 [00:00<00:08, 15

Saving twitter_stream_2020_01_31_full_ru.json.gz2:  82%|████████▏ | 11500/13965 [00:07<00:01, 1698.74it/s]
Saving twitter_stream_2020_01_31_full_ru.json.gz2:  84%|████████▎ | 11688/13965 [00:07<00:01, 1745.73it/s]
Saving twitter_stream_2020_01_31_full_ru.json.gz2:  85%|████████▌ | 11885/13965 [00:07<00:01, 1800.44it/s]
Saving twitter_stream_2020_01_31_full_ru.json.gz2:  86%|████████▋ | 12067/13965 [00:07<00:01, 1747.19it/s]
Saving twitter_stream_2020_01_31_full_ru.json.gz2:  88%|████████▊ | 12244/13965 [00:07<00:00, 1751.71it/s]
Saving twitter_stream_2020_01_31_full_ru.json.gz2:  89%|████████▉ | 12421/13965 [00:07<00:00, 1729.46it/s]
Saving twitter_stream_2020_01_31_full_ru.json.gz2:  90%|█████████ | 12600/13965 [00:07<00:00, 1743.52it/s]
Saving twitter_stream_2020_01_31_full_ru.json.gz2:  92%|█████████▏| 12788/13965 [00:07<00:00, 1771.26it/s]
Saving twitter_stream_2020_01_31_full_ru.json.gz2:  93%|█████████▎| 12966/13965 [00:07<00:00, 1701.91it/s]
Saving twitter_stream_2020_01_31_full

saved: twitter_stream_2020_01_31


In [5]:
extract_tweets_with_location_for_month(
    'archiveteam-twitter-stream-2020-10',
    '/Users/sismetanin/Downloads/archiveteam-twitter-stream-2020-10/',
)

Parsing *.ziparchiveteam-twitter-stream-2020-10:   0%|          | 0/31 [00:00<?, ?it/s]
Parsing twitter-stream-2020-10-01.zip:   6%|▌         | 87/1411 [03:10<58:35,  2.65s/it]


Parsing twitter-stream-2020-10-01.zip:  12%|█▏        | 175/1411 [06:17<35:32,  1.73s/it]


Parsing twitter-stream-2020-10-01.zip:  19%|█▊        | 263/1411 [08:53<31:34,  1.65s/it]


Parsing twitter-stream-2020-10-01.zip:  25%|██▍       | 351/1411 [11:45<38:30,  2.18s/it]


Parsing twitter-stream-2020-10-01.zip:  31%|███       | 439/1411 [14:04<25:03,  1.55s/it]


...

Parsing twitter-stream-2020-10-31.zip:  91%|█████████ | 1231/1351 [12:31<01:04,  1.85it/s]


Parsing twitter-stream-2020-10-31.zip:  98%|█████████▊| 1318/1351 [13:31<00:25,  1.29it/s]


Parsing twitter-stream-2020-10-31.zip: 100%|██████████| 1351/1351 [13:56<00:00,  1.26it/s]
                                                                                          
Saving twitter-stream-2020-10-31_full_ru.json.gz2:   0%|          | 0/15521 [00:00<?, ?it/s]
Saving twitter-stream-2020-10-31_full_ru.json.gz2:   2%|▏         | 335/15521 [00:00<00:04, 3345.05it/s]
Saving twitter-stream-2020-10-31_full_ru.json.gz2:   4%|▍         | 651/15521 [00:00<00:04, 3283.91it/s]
Saving twitter-stream-2020-10-31_full_ru.json.gz2:   6%|▋         | 998/15521 [00:00<00:04, 3327.09it/s]
Saving twitter-stream-2020-10-31_full_ru.json.gz2:   9%|▊         | 1326/15521 [00:00<00:04, 3309.05it/s]
Saving twitter-stream-2020-10-31_full_ru.json.gz2:  11%|█         | 1681/15521 [00:00<00:04, 3374.60it/s]
Saving twitter-stream-2020-10-31_full_ru.json.gz2:  13%|█▎        | 2034/15521 [00:00<00:03, 3415.70it/s]
Saving twitter-stream-2020-10-31_full_ru.json.gz2:  15%|█▌        | 2377/15521 [00:00<00:03,

Saving twitter-stream-2020-10-31_full_ru.json.gz2:  97%|█████████▋| 15099/15521 [00:04<00:00, 3207.64it/s]
Saving twitter-stream-2020-10-31_full_ru.json.gz2: 100%|██████████| 15521/15521 [00:04<00:00, 3289.62it/s]
Parsing *.ziparchiveteam-twitter-stream-2020-10: 100%|██████████| 31/31 [15:40:17<00:00, 1819.90s/it]


saved: twitter-stream-2020-10-31
